# Exploration

In [28]:
%pip install opencv-python imageio


[notice] A new release of pip is available: 25.1.1 -> 25.3
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


## Import

In [2]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from scipy.stats import gaussian_kde

## Data Processing

In [3]:
# Read the txt file (change the filename to yours)
data = np.loadtxt("data/23/rec0023_raw_audio_peak_target_points.txt")

# Reshape into columns of 3 (x, y, z)
points = data.reshape(-1, 3)

# Create a dataframe for clarity
df = pd.DataFrame(points, columns=["X", "Y", "Z"])

df.head()

X         Y         Z
0  2.045830 -1.480825  7.274045
1 -1.362152  1.511807  7.426236
2 -0.266157  2.565306  7.255230
3 -1.647605 -2.507390  7.091431
4 -2.028448 -1.777347  7.212242

In [36]:
len(df)

305

### Visualizing the data points

Let's first visualize the points in a 3D space.

In [4]:
fig = go.Figure(data=[go.Scatter3d(
    x=df["X"], y=df["Y"], z=df["Z"],
    mode='markers',
    marker=dict(
        size=3,
        opacity=0.7
    )
)])

fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z'
    ),
    title="3D Acoustic Points Visualization"
)

fig.show()

### Density map
Using a density map we can easily visualize the distribution of the data and where the most points are located.

In [7]:

## Calculating the KDE density
xyz = np.vstack([df["X"], df["Y"], df["Z"]])
kde = gaussian_kde(xyz, bw_method=0.2)

# Creating the grid in the space
x_range = np.linspace(df["X"].min(), df["X"].max(), 50)
y_range = np.linspace(df["Y"].min(), df["Y"].max(), 50)
z_range = np.linspace(0, 10, 50)
xx, yy, zz = np.meshgrid(x_range, y_range, z_range)
coords = np.vstack([xx.ravel(), yy.ravel(), zz.ravel()])

## Getting the estimated density for each point in the grid space
density = kde(coords).reshape(xx.shape)


In [8]:

fig = go.Figure(data=go.Volume(
    x=xx.flatten(),
    y=yy.flatten(),
    z=zz.flatten(),
    value=density.flatten(),
    isomin=np.quantile(density, 0.95), # Specify the minimum value for the density getting the quantile 95
    isomax=density.max(),
    opacity=0.20,  # lower = more transparent
    surface_count=15,  # number of contour layers
    colorscale='Inferno' 
))

fig.update_layout(
    scene=dict(
        xaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        yaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        zaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black', range=[0,10]),
    ),
    title="3D Density Heatmap of Acoustic Points"
)

fig.show()

### High Density Identification
We can identify where the high density is by counting the number of point in a predefined cube space.
We can bin the space into a grid and count the number of points in each bin.

In [9]:
cube_size = 0.5  # Cube dimensions

# Identifying the bin where each point belongs to
df["X_bin"] = np.floor(df["X"] / cube_size).astype(float)
df["Y_bin"] = np.floor(df["Y"] / cube_size).astype(float)
df["Z_bin"] = np.floor(df["Z"] / cube_size).astype(float)

# Count the number of points in each bin
cube_counts = (
    df.groupby(["X_bin", "Y_bin", "Z_bin"])
    .size()
    .reset_index(name="count")
)

# Getting the bin with the most points, this is the densest cube
max_cube = cube_counts.loc[cube_counts["count"].idxmax()]
x_bin, y_bin, z_bin = max_cube[["X_bin", "Y_bin", "Z_bin"]]
print(f"Most dense cube origin: ({x_bin}, {y_bin}, {z_bin}) — count = {max_cube['count']}")


Most dense cube origin: (-1.0, 1.0, 15.0) — count = 31.0


In [10]:
# Getting the coordinates of the cube
x0, y0, z0 = x_bin * cube_size, y_bin * cube_size, z_bin * cube_size
x1, y1, z1 = x0 + cube_size, y0 + cube_size, z0 + cube_size

# Getting the points inside the cube
inside = df[
    (df["X"] >= x0) & (df["X"] < x1) &
    (df["Y"] >= y0) & (df["Y"] < y1) &
    (df["Z"] >= z0) & (df["Z"] < z1)
]

In [11]:
fig = go.Figure()

# Plot all points (light gray)
fig.add_trace(go.Scatter3d(
    x=df["X"], y=df["Y"], z=df["Z"],
    mode='markers',
    marker=dict(size=3, color='lightgray', opacity=0.3),
    name="All Points"
))

# Highlight points inside the high-density cube (red)
fig.add_trace(go.Scatter3d(
    x=inside["X"], y=inside["Y"], z=inside["Z"],
    mode='markers',
    marker=dict(size=5, color='red'),
    name="Points in High-Density Cube"
))

# Draw the cube as a wireframe
fig.add_trace(go.Mesh3d(
    x=[x0, x1, x1, x0, x0, x1, x1, x0],
    y=[y0, y0, y1, y1, y0, y0, y1, y1],
    z=[z0, z0, z0, z0, z1, z1, z1, z1],
    color='red',
    opacity=0.2,
    alphahull=0,
    name="High-Density Cube"
))

fig.update_layout(
    scene=dict(
        xaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        yaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        zaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black', range=[0,10]),
    ),
    title="Cube with Highest Point Density"
)

fig.show()

## Editing Video

In [57]:
import math
def compute_coordinates(df, n_frames, start_frame_index):
    
    # Ensure the input has the needed columns
    if not {'X', 'Y'}.issubset(df.columns):
        raise ValueError("DataFrame must have 'X' and 'Y' columns.")

    total_points = len(df)
    points_per_frame = math.floor(total_points / n_frames)

    coords = []

    for i in range(start_frame_index, n_frames):
        # Get indices of coordinates to use in this frame
        start = max(0, points_per_frame *(i - 1) - 20)
        end = int((i) * points_per_frame)
        subset = df.iloc[start:end]

        if subset.empty:
            coords.append((np.nan, np.nan))
            continue

        # Remove outliers using IQR (Interquartile Range)
        for col in ['X', 'Y']:
            Q1 = subset[col].quantile(0.25)
            Q3 = subset[col].quantile(0.75)
            IQR = Q3 - Q1
            subset = subset[
                (subset[col] >= Q1 - 1.5 * IQR) &
                (subset[col] <= Q3 + 1.5 * IQR)
            ]

        # Average remaining points
        x_mean = subset['X'].mean()
        y_mean = subset['Y'].mean()

        coords.append((x_mean, y_mean))

    return coords

In [53]:
def transform_coordinates(x, y, width, height):
    # Convert from [-2, 2] to [0, 1]
    x_norm = (x + 2) / 4.0
    y_norm = (y + 2) / 4.0
    
    # Scale to video dimensions and convert to integers
    x_pixel = int(round(x_norm * (width - 1)))
    y_pixel = int(round(y_norm * (height - 1)))
    
    # Ensure coordinates are within bounds
    x_pixel = max(0, min(x_pixel, width - 1))
    y_pixel = max(0, min(y_pixel, height - 1))
    
    return x_pixel, y_pixel

[(49, 62), (44, 68), (54, 63), (51, 63), (48, 64), (56, 61), (49, 48), (57, 48), (49, 59), (62, 50), (59, 47), (55, 51), (59, 58), (63, 57), (65, 54), (66, 62), (70, 59), (68, 63), (71, 63), (63, 63), (61, 76), (49, 72), (47, 81), (56, 86), (51, 92), (52, 89), (42, 67), (51, 72), (46, 64), (35, 54), (33, 56), (39, 56), (53, 59), (52, 61), (58, 51), (62, 50), (66, 44), (67, 34), (59, 37), (55, 31), (47, 45), (46, 52), (46, 57), (46, 61), (44, 69), (45, 74), (38, 82), (30, 65), (29, 64), (30, 70), (39, 71), (33, 60), (36, 64), (45, 70), (47, 69), (51, 70), (61, 52), (58, 74), (59, 77), (60, 76), (59, 82), (54, 85), (46, 79), (40, 52), (41, 76), (35, 51), (34, 47), (31, 47), (28, 58), (41, 60), (50, 56), (54, 56), (57, 48), (57, 53), (67, 44), (65, 56), (60, 55), (69, 54), (62, 70), (51, 69), (41, 73), (51, 58), (50, 53), (46, 60), (55, 54), (64, 67), (68, 65), (55, 65), (55, 77), (57, 78), (43, 84), (40, 64), (51, 65), (61, 73), (61, 74), (59, 69), (61, 75), (54, 76), (52, 64), (49, 67)]

In [ ]:

import cv2
import numpy as np
import os
from IPython.display import Video

# Input and output video paths
input_path = "data/23/video23.mp4"
output_path = "output_with_square.mp4"

# Open the video file
cap = cv2.VideoCapture(input_path)
if not cap.isOpened():
    raise ValueError("❌ Could not open input video. Check the path or format.")

# Get video properties
n_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
fps = cap.get(cv2.CAP_PROP_FPS)
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

# Computing coordinates of the square
START_FRAME = 20
square_coordinates = compute_coordinates(df, n_frames, START_FRAME)

# Transforming coordinates
transformed_coord = []
for i in range(len(square_coordinates)):
    x = square_coordinates[i][0]
    y = square_coordinates[i][1]
    # Using the same width as height to keep the square shape of the video
    transformed_coord.append(transform_coordinates(x, y, width = (width - 1), height = (width - 1)))


# Use a codec that works on macOS (MP4 with 'avc1')
fourcc = cv2.VideoWriter_fourcc(*'avc1')
out = cv2.VideoWriter(output_path, fourcc, fps, (width, height))

square_size = 50
frame_idx = 0

while True:
    ret, frame = cap.read()
    if not ret:
        break

    if(frame_idx >= START_FRAME):
        idx = frame_idx - START_FRAME
        # Move the square in a small circular motion
        x = int(transformed_coord[idx][0])
        y = int(transformed_coord[idx][1])

        # Draw only the frame (no fill)
        thickness = 3  # line width
        cv2.rectangle(frame, (x, y), (x + square_size, y + square_size), (0, 0, 255), thickness)


    out.write(frame)
    frame_idx += 1

cap.release()
out.release()
cv2.destroyAllWindows()

print("✅ Video created:", output_path)
print("Frames:", frame_idx)
Video(output_path, embed=True)

✅ Video created: output_with_square.mp4
Frames: 132
